In [ ]:
import json
import random

# Define the path to the full Yelp dataset file
full_data_path = "yelp_academic_dataset_review.json"

# Define the path to save the sampled dataset file
sampled_data_path = "yelp_academic_dataset_review_sampled.json"

# Define the number of reviews to sample (adjust as needed)
num_reviews_to_sample = 10000  # Example: Sample 10,000 reviews

# Load all reviews from the full dataset
all_reviews = []
with open(full_data_path, "r", encoding="utf-8") as f:
    for line in f:
        review = json.loads(line)
        all_reviews.append(review)

# Randomly sample a subset of reviews
sampled_reviews = random.sample(all_reviews, num_reviews_to_sample)

# Save the sampled reviews to a new JSON file
with open(sampled_data_path, "w", encoding="utf-8") as f:
    for review in sampled_reviews:
        json.dump(review, f)
        f.write("\n")

print(f"Sampled {num_reviews_to_sample} reviews and saved to {sampled_data_path}")


In [ ]:
import gzip

# Define the path to save the compressed dataset file
compressed_data_path = "yelp_academic_dataset_review_sampled.json.gz"

# Compress the sampled dataset file using gzip
with open(sampled_data_path, "rb") as f_in:
    with gzip.open(compressed_data_path, "wb") as f_out:
        f_out.writelines(f_in)

print(f"Compressed file saved to {compressed_data_path}")


In [1]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import classification_report, accuracy_score

# Load the preprocessed Yelp dataset (sampled and compressed if applicable)
data_path = "yelp_academic_dataset_review_sampled.json.gz"  # Adjust the path
data = pd.read_json(data_path, lines=True)

In [2]:
data

review_id                 user_id             business_id  \
0     f9khuhJxadQhg6CaI1cRdA  4Qijwb2RDiUGc4SBjA2lJg  nTBStZYJfHGdSZJbpaBiPA   
1     WH0c1wEMu4XRTIysI7uMig  7JeW4Mlvqdp7R-FAUBB_vA  H3Tmgv94pbGvBIKZ4Rs9Cw   
2     S1Lg07IGrupUDk7Uu9rnQQ  umUy5DTpVrvQDXLR4gywHA  H7BikysfQbS9bMULQsCU_Q   
3     AH4_Pua0yzK4oU9FoU8hXQ  uwYw0KKj16lC_nq_HsQGVQ  Xb6QfBbleg2aJT2cG807jQ   
4     9_CIDS98p6ZsTRiCvmuIKA  l9bVKgzvjjcU8Iang3Tvtg  lqSJkyNSE1yPeux4PoR-pg   
...                      ...                     ...                     ...   
9995  5MknizHCBH3jpj5DJd-6Uw  d2VrfngFJ1f1nvNAsojJzw  hy-E7DdXbdgTbwphKUYW1w   
9996  mXFlaWuiCnyCkZ_SIAGqew  cHWDGVf4LofBk9wZ2mnXQQ  AYWSFv6QxF5IjQSxITMUug   
9997  W1Ij-zC3ufRU5MTEgHLjmg  aN9nWudz5rfar7rHr9lHfA  oyJ3gXNkV0DO0YxcaTgtTg   
9998  HNejB5H9iD1qe3MMKxg6sg  6JejVLZl5M-IB3UkNTkXtQ  WJLKQTduGumxjlXelqiuKg   
9999  LSJGzHJ7whqNn5uPxidMjQ  _Av1LaAAY0Y8YcPp7Ck7fg  M983OPfVRnwvG7zEOzykCA   

      stars  useful  funny  cool  \
0         4       1      0     1   
1         5       1      0     1   
2         2       4      1     0   
3         1       1      0     0   
4         1       0      0     0   
...     ...     ...    ...   ...   
9995      1       1      0     0   
9996      5       0      0     0   
9997      5       0      0     0   
9998      3       0      0     0   
9999      5       0      0     0   

                                                   text                date  
0     I had read about this place adding a second lo... 2011-02-08 17:48:40  
1     I had dinner at Tin Angel on Saturday and was ... 2012-04-16 13:30:02  
2     I was really excited to visit the store, havin... 2019-10-05 00:17:15  
3     I hired Two Men and a Truck for my recent move... 2016-06-02 13:27:24  
4     i was very disappointed to this company. They ... 2020-06-05 22:28:47  
...                                                 ...                 ...  
9995  This was such a trash experience. We signed up... 2021-07-29 16:10:10  
9996  I have been going to Goshen Nail Salon for the... 2018-03-16 00:30:50  
9997  Ok. This place surprised me. I always thought ... 2018-06-01 23:56:44  
9998  Meets expectations, but quirky.  The trucks re... 2016-06-29 15:57:34  
9999  Jordan was our waiter. He was very attentive a... 2017-03-15 23:54:07  

[10000 rows x 9 columns]

In [3]:
# Map stars to sentiment labels
def map_sentiment(stars):
    if stars >= 4:
        return "positive"
    elif stars <= 2:
        return "negative"
    else:
        return "neutral"  # Optional: Handle neutral sentiment if needed

# Apply sentiment mapping to stars
data['sentiment'] = data['stars'].apply(map_sentiment)


In [4]:
# Apply sentiment mapping to stars
data['sentiment'] = data['stars'].apply(map_sentiment)

# Split the data into training and testing sets
train_data, test_data = train_test_split(data, test_size=0.2, random_state=42)

# Save the preprocessed data
train_data.to_csv("preprocessed_train_data.csv", index=False)
test_data.to_csv("preprocessed_test_data.csv", index=False)

In [ ]:
pip install torch


In [ ]:
pip install transformers

In [ ]:
import pandas as pd
import torch
from transformers import BertTokenizer, BertForSequenceClassification, Trainer, TrainingArguments
from sklearn.metrics import accuracy_score, precision_recall_fscore_support

# Load the preprocessed training and testing data
train_data = pd.read_csv("preprocessed_train_data.csv")  # Adjust the path
test_data = pd.read_csv("preprocessed_test_data.csv")  # Adjust the path
